# Fix pathing

In [1]:
import sys


sys.path.append("..")


In [2]:
import constants

import os


constants.PROJECT_DIRECTORY_PATH = os.path.dirname(os.path.dirname(constants.PROJECT_DIRECTORY_PATH))


# Init

In [3]:
import datahandler

import matplotlib.pyplot as plt


dataset_id = "oslo"

data_preprocessor = datahandler.DataPreprocessorOUS(dataset_id)
data_preprocessor.execute()

data_loader = datahandler.DataLoader(dataset_id)
data_loader.execute()


Loading dataset: 100%|██████████| 6/6 [00:42<00:00,  7.03s/it]


# Analysis
- All of the rows where "time_available" is NaN should be dropped (64 rows)
- All of the rows where "time_dispatch" is NaN should be dropped (111 rows)
- All of the rows where "triage_impression_during_call" is NaN should be dropped (9 rows)
- All of the rows where "time_arrival_scene" is NaN and "time_arrival_hospital" is not NaN should be dropped (13695 rows)
- All of the rows where "time_departure_scene" is NaN and "time_arrival_hospital" is not NaN should be dropped (8356 rows)


In [4]:
nan_rows = data_loader.processed_incidents_df[data_loader.processed_incidents_df["time_available"].isna()]
print(nan_rows.shape[0])


64


In [5]:
nan_rows = data_loader.processed_incidents_df[data_loader.processed_incidents_df["time_dispatch"].isna()]
print(nan_rows.shape[0])

23104


In [6]:
nan_rows = data_loader.processed_incidents_df[data_loader.processed_incidents_df["triage_impression_during_call"].isna()]
print(nan_rows.shape[0])

9


In [7]:
count = data_loader.processed_incidents_df[(data_loader.processed_incidents_df["time_arrival_scene"].isna()) & (~data_loader.processed_incidents_df["time_arrival_hospital"].isna())].shape[0]
print(count)

13695


In [8]:
count = data_loader.processed_incidents_df[(data_loader.processed_incidents_df["time_departure_scene"].isna()) & (~data_loader.processed_incidents_df["time_arrival_hospital"].isna())].shape[0]
print(count)

8356


In [9]:
print(data_loader.enhanced_incidents_df.shape)

(711924, 19)


In [10]:
print(data_loader.enhanced_incidents_df["response_time_sec"])

0            NaN
1            NaN
2            NaN
3            NaN
4            NaN
           ...  
711919    1125.0
711920    1773.0
711921    1449.0
711922    5527.0
711923    2357.0
Name: response_time_sec, Length: 711924, dtype: float64


In [17]:
df = data_loader.enhanced_incidents_df

df[["longitude", "latitude", "easting", "northing", "grid_id", "grid_row", "grid_col"]].head()

longitude   latitude  easting  northing     grid_id  grid_row  grid_col
0  59.754322  10.807072   264500   6631500  1939046988      6631       264
1  59.835487  10.814718   265500   6640500  -945845900      6640       265
2  59.658400  10.623601   253500   6621500  -686780612      6621       253
3  59.950684  11.051121   279500   6652500  1615212628      6652       279
4  59.930060  10.964014   274500   6650500 -1140149116      6650       274

In [21]:
import folium

df_new = df[100000:110000]

# Create a folium map centered around the median values of the latitudes and longitudes
m = folium.Map(location=[df_new.latitude.median(), df_new.longitude.median()], zoom_start=10)

# Constants to convert meters to latitude and longitude degrees approximately
# These values can be more accurate depending on the location and the projection used
METERS_IN_DEG_LAT = 0.008983 # 1 km in latitude degrees roughly
METERS_IN_DEG_LON = 0.014485 # 1 km in longitude degrees at 60 degrees latitude roughly

for index, row in df_new.iterrows():
    southwest = [row['latitude'], row['longitude']]
    northeast = [row['latitude'] + METERS_IN_DEG_LAT, row['longitude'] + METERS_IN_DEG_LON]
    
    # Plotting a rectangle to represent the grid cell
    folium.Rectangle(
        bounds=[southwest, northeast],
        color='blue',
        fill=True,
        fill_color='blue',
        fill_opacity=0.2
    ).add_to(m)

# Save the map as an HTML file
m